## Installing Pytorch

In [1]:
# http://pytorch.org/
from os.path import exists
from wheel.pep425tags import get_abbr_impl, get_impl_ver, get_abi_tag
platform = '{}{}-{}'.format(get_abbr_impl(), get_impl_ver(), get_abi_tag())
cuda_output = !ldconfig -p|grep cudart.so|sed -e 's/.*\.\([0-9]*\)\.\([0-9]*\)$/cu\1\2/'
accelerator = cuda_output[0] if exists('/dev/nvidia0') else 'cpu'

!pip install -q http://download.pytorch.org/whl/{accelerator}/torch-0.4.1-{platform}-linux_x86_64.whl torchvision
import torch

tcmalloc: large alloc 1073750016 bytes == 0x57f4e000 @  0x7f88843f62a4 0x591a07 0x5b5d56 0x502e9a 0x506859 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x502209 0x502f3d 0x506859 0x504c28 0x502540 0x502f3d 0x507641 0x504c28 0x502540 0x502f3d 0x507641
fastai 1.0.41 has requirement torch>=1.0.0, but you'll have torch 0.4.1 which is incompatible.


## Building Fairseq

In [3]:
!git clone https://github.com/pytorch/fairseq.git
import os
os.chdir("fairseq/")
!pip install -r requirements.txt
%run -i 'setup.py' build develop

Cloning into 'fairseq'...
remote: Enumerating objects: 127, done.
remote: Counting objects: 100% (127/127), done.
remote: Compressing objects: 100% (85/85), done.
remote: Total 3436 (delta 56), reused 72 (delta 32), pack-reused 3309
Receiving objects: 100% (3436/3436), 3.34 MiB | 1.05 MiB/s, done.
Resolving deltas: 100% (2480/2480), done.
running build
running build_py
creating build
creating build/lib.linux-x86_64-3.6
creating build/lib.linux-x86_64-3.6/fairseq
copying fairseq/__init__.py -> build/lib.linux-x86_64-3.6/fairseq
copying fairseq/search.py -> build/lib.linux-x86_64-3.6/fairseq
copying fairseq/sequence_scorer.py -> build/lib.linux-x86_64-3.6/fairseq
copying fairseq/distributed_utils.py -> build/lib.linux-x86_64-3.6/fairseq
copying fairseq/tokenizer.py -> build/lib.linux-x86_64-3.6/fairseq
copying fairseq/legacy_distributed_data_parallel.py -> build/lib.linux-x86_64-3.6/fairseq
copying fairseq/meters.py -> build/lib.linux-x86_64-3.6/fairseq
copying fairseq/trainer.py -> buil

## Model for Tn


### Data

In [4]:
!git clone https://github.com/LauraMartinus/ukuxhumana.git

Cloning into 'ukuxhumana'...
remote: Enumerating objects: 139, done.
remote: Counting objects: 100% (139/139), done.
remote: Compressing objects: 100% (116/116), done.
remote: Total 1405 (delta 67), reused 61 (delta 23), pack-reused 1266
Receiving objects: 100% (1405/1405), 405.42 MiB | 20.19 MiB/s, done.
Resolving deltas: 100% (674/674), done.
Checking out files: 100% (308/308), done.


### Subword

In [5]:
!git clone https://github.com/rsennrich/subword-nmt

Cloning into 'subword-nmt'...
remote: Enumerating objects: 28, done.
remote: Counting objects: 100% (28/28), done.
remote: Compressing objects: 100% (26/26), done.
remote: Total 509 (delta 14), reused 10 (delta 2), pack-reused 481
Receiving objects: 100% (509/509), 216.68 KiB | 853.00 KiB/s, done.
Resolving deltas: 100% (301/301), done.


In [0]:
#os.chdir('../')
!ls

## Study


**4k**

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 4000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

**8k**

In [0]:
#os.chdir('../')
!ls

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 8000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

**12k**

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 12000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

**16k**

In [0]:
#os.chdir('content/')
!ls

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 16000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

**20k**

In [0]:
!ls

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 20.000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='entn.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Pleas

**24k**

In [6]:
!ls

build		 fairseq	   interactive.py  requirements.txt  tests
CONTRIBUTING.md  fairseq.egg-info  LICENSE	   score.py	     train.py
docs		 fairseq.gif	   PATENTS	   scripts	     ukuxhumana
eval_lm.py	 fairseq_logo.png  preprocess.py   setup.py
examples	 generate.py	   README.md	   subword-nmt


In [7]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 24000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

fairseq/subword-nmt/learn_bpe.py:267: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Please point to the new location, or install the package and use the command 'subword-nmt'
  DeprecationWarning
fairseq/subword-nmt/apply_bpe.py:351: ResourceWarning: unclosed file <_io.TextIOWrapper name='entn.codes' mode='r' encoding='UTF-8'>
  args.codes = codecs.open(args.codes.name, encoding='utf-8')
fairseq/subword-nmt/apply_bpe.py:334: DeprecationWarning: this script's location has moved to /content/fairseq/subword-nmt/subword_nmt. This symbolic link will be removed in a future version. Pleas

**28k**

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 28000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

**32k**

In [0]:
!ls

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 32000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

**36k**

In [0]:
#os.chdir('fairseq/')
!ls

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 36000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

**40k**

In [0]:
!ls

In [0]:
os.chdir('../')
!cat fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > combine.txt
!fairseq/subword-nmt/learn_bpe.py -s 40000 <combine.txt> entn.codes

!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.en > train.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.train.tn > train.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.en > valid.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.dev.tn > valid.tn
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.en > test.en
!fairseq/subword-nmt/apply_bpe.py -c entn.codes < fairseq/ukuxhumana/clean/en_tn/entn_parallel.test.tn > test.tn

os.chdir('fairseq/')
TEXT=".."
%run 'preprocess.py' --source-lang en --target-lang tn --trainpref $TEXT/train --validpref $TEXT/valid --testpref $TEXT/test --destdir data-bin/entn

!mkdir -p checkpoint/fconv
!python train.py data-bin/entn \
    --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv --save-dir checkpoint/fconv

# for sentencepiece remove ▁
output = %run 'generate.py' data-bin/entn --path checkpoint/fconv/checkpoint_best.pt --beam 5 --batch-size 128 --remove-bpe --source-lang en --target-lang tn

## Results

*   40k: 
*   36k: 
*   32k: 26.18
*   28k: 
*   24k: 25.34
*   20k: 22.09
*   16k: 26.03
*   12k: 25.62
*     8k: 21.28
*     4k: 24.34

